In [0]:
import pandas as pd
from pyspark.sql import SparkSession

In [0]:
spark = SparkSession.builder \
    .appName("Data Quality Checks") \
    .getOrCreate()

In [0]:
data = spark.read.format("delta").load("dbfs:/user/hive/warehouse/researchdata",header = True)

In [0]:
from pyspark.sql.functions import count, when, isnull

null_counts = data.select([count(when(isnull(c), c)).alias(c) for c in data.columns]).toPandas().transpose()

In [0]:
print(null_counts)

                            0
Variable                    0
Breakdown                   0
Breakdown_category          0
Year                        0
RD_Value                    0
Status                   4461
Unit                        0
Footnotes                   0
Relative_Sampling_Error     0


In [0]:
duplicate_count = data.groupBy(data.columns).count().filter('count > 1').count()


In [0]:
print(duplicate_count)

25


In [0]:
data.dtypes


[('Variable', 'string'),
 ('Breakdown', 'string'),
 ('Breakdown_category', 'string'),
 ('Year', 'bigint'),
 ('RD_Value', 'string'),
 ('Status', 'string'),
 ('Unit', 'string'),
 ('Footnotes', 'string'),
 ('Relative_Sampling_Error', 'string')]

In [0]:
df = data

In [0]:
from pyspark.sql.functions import col

filtered_df = df.filter(col("Year") > 2015)
filtered_df.show()


+--------------------+--------------+--------------------+----+--------+------+--------------------+---------+-----------------------+
|            Variable|     Breakdown|  Breakdown_category|Year|RD_Value|Status|                Unit|Footnotes|Relative_Sampling_Error|
+--------------------+--------------+--------------------+----+--------+------+--------------------+---------+-----------------------+
|_01_Total_RD_Expe...|ANZSIC_1_Digit|A_Agriculture, Fo...|2016|      91|  NULL|NZ Dollars (milli...|       12|                   23.8|
|_01_Total_RD_Expe...|ANZSIC_1_Digit|A_Agriculture, Fo...|2018|      89|  NULL|NZ Dollars (milli...|       12|                   51.7|
|_01_Total_RD_Expe...|ANZSIC_1_Digit|A_Agriculture, Fo...|2019|     ...|  NULL|NZ Dollars (milli...|       12|                    ...|
|_01_Total_RD_Expe...|ANZSIC_1_Digit|A_Agriculture, Fo...|2020|      99|  NULL|NZ Dollars (milli...|       12|                   30.2|
|_01_Total_RD_Expe...|ANZSIC_1_Digit|A_Agriculture, Fo.

In [0]:
from pyspark.sql.functions import length, avg

# Calculate distinct values, null count, and average value length for each column
column_profiles = []

for col in df.columns:
    distinct_values = df.select(col).distinct().count()
    null_count = df.filter(df[col].isNull()).count()
    avg_value_length = df.select(avg(length(col))).collect()[0][0]
    column_profiles.append((col, distinct_values, null_count, avg_value_length))

# Print column profiles
print("Column Profiling:")
for col_profile in column_profiles:
    col, distinct_values, null_count, avg_value_length = col_profile
    print(f"Column: {col}, Distinct Values: {distinct_values}, Null Count: {null_count}, Average Value Length: {avg_value_length}")

print("\n")


Column Profiling:
Column: Variable, Distinct Values: 18, Null Count: 0, Average Value Length: 61.604074223477205
Column: Breakdown, Distinct Values: 6, Null Count: 0, Average Value Length: 12.772488906817266
Column: Breakdown_category, Distinct Values: 47, Null Count: 0, Average Value Length: 27.603670835014118
Column: Year, Distinct Values: 6, Null Count: 0, Average Value Length: 4.0
Column: RD_Value, Distinct Values: 523, Null Count: 0, Average Value Length: 2.199273900766438
Column: Status, Distinct Values: 3, Null Count: 4461, Average Value Length: 1.0
Column: Unit, Distinct Values: 2, Null Count: 0, Average Value Length: 21.0
Column: Footnotes, Distinct Values: 32, Null Count: 0, Average Value Length: 13.72125857200484
Column: Relative_Sampling_Error, Distinct Values: 883, Null Count: 0, Average Value Length: 2.923961274707543




In [0]:
from pyspark.sql.functions import col, count, when

# Check for missing values
print("Missing Values:")
missing_values = df.select([count(when(col(c).isNull(), c)).alias(c) for c in df.columns])
missing_values.show()


Missing Values:
+--------+---------+------------------+----+--------+------+----+---------+-----------------------+
|Variable|Breakdown|Breakdown_category|Year|RD_Value|Status|Unit|Footnotes|Relative_Sampling_Error|
+--------+---------+------------------+----+--------+------+----+---------+-----------------------+
|       0|        0|                 0|   0|       0|  4461|   0|        0|                      0|
+--------+---------+------------------+----+--------+------+----+---------+-----------------------+



In [0]:
df.describe().display()

summary Variable Breakdown Breakdown_category Year RD_Value Status Unit Footnotes Relative_Sampling_Error count 4958 4958 4958 4958 4958 497 4958 4958 4958 mean null null null 2019.3366276724485 181.74131589701676 null null 12.0 42.06354720065388 stddev null null null 1.9701816101309002 410.3988294378914 null null 0.0 47.72459467829779 min _01_Total_RD_Expenditure ANZSIC_1_Digit 01_Business Sector 2016 .. P NZ Dollars (millions) 1 and 12 .. max _11_Broad_purpose_of_research:_Primary_Industries Total Total 2022 C R Number of enterprises 8 and 12 and 28 C

In [0]:
data.display()

Variable Breakdown Breakdown_category Year RD_Value Status Unit Footnotes Relative_Sampling_Error _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2016 91 null NZ Dollars (millions) 12 23.8 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2018 89 null NZ Dollars (millions) 12 51.7 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2020 99 null NZ Dollars (millions) 12 30.2 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2022 94 P NZ Dollars (millions) 12 40.4 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2016 5 null NZ Dollars (millions) 3 and 12 38.3 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2018 9 null NZ Dollars (millions) 3 and 12 177.1 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2019 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2020 2 null NZ Dollars (millions) 3 and 12 62.6 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2021 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2022 4 P NZ Dollars (millions) 3 and 12 106.8 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2016 671 null NZ Dollars (millions) 12 8.4 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2018 673 null NZ Dollars (millions) 12 10 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2020 825 null NZ Dollars (millions) 12 7.6 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2022 795 P NZ Dollars (millions) 12 7.3 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2016 6 null NZ Dollars (millions) 3 and 12 44 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2018 6 null NZ Dollars (millions) 3 and 12 60.1 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2019 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2020 26 null NZ Dollars (millions) 3 and 12 40 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2021 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2022 36 P NZ Dollars (millions) 3 and 12 64.1 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2016 13 null NZ Dollars (millions) 12 103.7 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2018 11 null NZ Dollars (millions) 12 49.6 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2020 23 null NZ Dollars (millions) 12 46.8 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2022 28 P NZ Dollars (millions) 12 46.1 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2016 111 null NZ Dollars (millions) 12 17.3 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2018 233 null NZ Dollars (millions) 12 40.3 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2020 174 null NZ Dollars (millions) 12 21 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2022 193 P NZ Dollars (millions) 12 11.1 _01_Total_RD_Expenditure ANZSIC_

Databricks visualization. Run in Databricks to view.

In [0]:
data.display()

Variable Breakdown Breakdown_category Year RD_Value Status Unit Footnotes Relative_Sampling_Error _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2016 91 null NZ Dollars (millions) 12 23.8 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2018 89 null NZ Dollars (millions) 12 51.7 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2020 99 null NZ Dollars (millions) 12 30.2 _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit A_Agriculture, Forestry and Fishing 2022 94 P NZ Dollars (millions) 12 40.4 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2016 5 null NZ Dollars (millions) 3 and 12 38.3 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2018 9 null NZ Dollars (millions) 3 and 12 177.1 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2019 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2020 2 null NZ Dollars (millions) 3 and 12 62.6 _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2021 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit B_Mining 2022 4 P NZ Dollars (millions) 3 and 12 106.8 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2016 671 null NZ Dollars (millions) 12 8.4 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2018 673 null NZ Dollars (millions) 12 10 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2020 825 null NZ Dollars (millions) 12 7.6 _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit C_Manufacturing 2022 795 P NZ Dollars (millions) 12 7.3 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2016 6 null NZ Dollars (millions) 3 and 12 44 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2018 6 null NZ Dollars (millions) 3 and 12 60.1 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2019 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2020 26 null NZ Dollars (millions) 3 and 12 40 _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2021 ... null NZ Dollars (millions) 3 and 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit D_Electricity, Gas, Water and Waste Services 2022 36 P NZ Dollars (millions) 3 and 12 64.1 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2016 13 null NZ Dollars (millions) 12 103.7 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2018 11 null NZ Dollars (millions) 12 49.6 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2020 23 null NZ Dollars (millions) 12 46.8 _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit E_Construction 2022 28 P NZ Dollars (millions) 12 46.1 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2016 111 null NZ Dollars (millions) 12 17.3 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2018 233 null NZ Dollars (millions) 12 40.3 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2019 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2020 174 null NZ Dollars (millions) 12 21 _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2021 ... null NZ Dollars (millions) 12 ... _01_Total_RD_Expenditure ANZSIC_1_Digit F_Wholesale Trade 2022 193 P NZ Dollars (millions) 12 11.1 _01_Total_RD_Expenditure ANZSIC_

Databricks visualization. Run in Databricks to view.